My final project, I'm going to implement the finite difference method for solving partial differential equations



In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.tri as tri

In [ ]:
class boundary:
    def __init__(self,boundaryPoints): #stores boundary points as an n by 2  array of numbers
        
        self.boundaryPoints=np.concatenate((boundaryPoints,[boundaryPoints[0]]))
    def plot(x):
        plt.plot(x.boundaryPoints[:,0],x.boundaryPoints[:,1])
    def scatter(x):
        plt.scatter(x.boundaryPoints[:,0],x.boundaryPoints[:,1])
    def append(B,x): #supposed to create a new boundary which has the same boundary points as 
        #B but with x appended to B . 
        y=[]
        X=B.boundaryPoints
        for i in range(B.boundaryPoints.shape[0]-1):
            y+=[[X[i,0],X[i,1]]]
        y+=[[x[0],x[1]]]
        return boundary(np.array(y))
        
def createBoundary(f,a,b,n):
    BP=np.array([f(i) for i in np.linspace(a,b,num=n)]+[f(a)])
    return boundary(BP)

In [ ]:
x=boundary(np.array([[0,0],[2,3],[4,3],[6,0],[4,0],[3.5,1],[2.5,1],[2,0],[0,0],[2.5,1.5],[3.5,1.5],[3,2],[2.5,1.5]]))

In [ ]:
dataForP=np.array([[2,2],[4,2],[4,4],[0,4],[0,0],[2,0],[2,2],[2,2.5],[3.5,2.5],[3.5,3.5],[2,3.5],[2,2.5]])
P=boundary(dataForP)
#boundary.plot(P)
Σ=boundary(np.array([[0,0],[1,0],[0.5,0.5],[1,1],[0,1]]))
#boundary.plot(Σ)
Σ2=boundary.append(Σ,[0,0.5])


In [ ]:
def edgeIntersect(x0,x1,x2):
    y=[min(x1[1],x2[1]),max(x1[1],x2[1])]
    if not((x0[1]<=y[1]) and (x0[1]>y[0])):
        return (False)
    else :
        t= (x0[1]-x1[1])/(x2[1]-x1[1])
        return (x0[0]<=x1[0]+(x2[0]-x1[0])*t)
def onEdge(x0,x1,x2,tol=1e-7): #tests if a point is on the edge of a line segment 
    #z0=(z1)+(z2-z1)t
    
    z0=complex(x0[0],x0[1])
    z1=complex(x1[0],x1[1])
    z2=complex(x2[0],x2[1])
    return abs(np.imag((z0-z1)/(z2-z1)))<tol and np.real((z0-z1)/(z2-z1))<=1 and 0<=np.real((z0-z1)/(z2-z1))  #z0
#on the edge between (z1) and z2 iff (z0-z1)/(z2-z1) is real and in [0,1]. 

def pointOnBoundary(x,B):
    BP=B.boundaryPoints
    for i in range(len(BP)-1):
        if (onEdge(x,BP[i],BP[i+1])):
            return True
    return False 

        
    
    #(1+t,2)=(2.0+2.0s,2.0+2.0s). 
    #this intersects iff x0[1]=2.0+2.0s for s in [0,1]
    #if s0 in [min(y0,y1),max(y0,y1)]
onEdge([0,0.5],[0,0],[0,1])
edgeIntersect([0.2,0.2],[0.5,0.5],[1,0])

In [ ]:
from matplotlib import cm

In [ ]:
def pointInBoundary(x,B):
    BP=B.boundaryPoints
    crossingNumber=0
    for i in range(len(BP)-1):
        if (edgeIntersect(x,BP[i],BP[i+1])):
            #print(BP[i],BP[i+1])
            #print(True)
            crossingNumber+=1
    #print(crossingNumber)
    if (crossingNumber%2==0):
        return False
    return True


print(edgeIntersect([0.6,0.5],[1,0],[0.5,0.5]))

In [ ]:
#This cell contains all the initializations
CircuitBoard=boundary(np.array([[0,0],[0,2.5],[2,2.5],[2,4],[6,4],[7,3.5],[7,0.5],[6,0]]))

semiconductorList=np.array([
    boundary(np.array([[0.5,1],[0.5,1.5],[1,1.5],[1,1]])),
    boundary(np.array([[5,1],[5.5,1],[5.5,1.5],[5,1.5]])),
    boundary(np.array([[5,3],[5.5,3],[5.5,3.5],[5,3.5]])),
    boundary(np.array([[2.5,2],[2.8,2],[2.8,2.5],[2.5,2.5]]))
])

#ToDo 
#hardcoded, take the centers of every bounday in semiconductorarray?
connectorArray=np.array([[0.75,1.25],[5.25,1.25],[5.25,3.25],[2.65,2.25]])  


x=np.linspace(-1, 8, 101)
y=np.linspace(-1, 8, 101)
X,Y=np.meshgrid(x,y)

#Wire Constants
specificHeatCopper=0.385 #this is in j/g
densityOfCopper = 8.96 # g/cm^3
resistanceOfCopperWire = 0.000331 #This is ohm/cm --> AWG 20 gauge copper is 33.31 ohm/km
currentReducingFactor = 0.5 #This is used to test different current conditions
currentI1 = 300/1000 # This is 300mA
currentI2 = 170/1000 # This is 100mA
currentI3 = 250/1000 # This is 150mA
currentI4 = 300/1000 # This is 500mA
wireThicknessRatio = 70 #(test 3) # 35 (test 2) #(test-1) --> 70

#chip-constant modelling the slope of temperature rise
chipConstant = 72

#Base Temperature of the board
baseTemperature = 30 #This is the room temperature (or ambient temperature)
proposedLevels = [25,30,35,36,40, 41,42,43, 45, 50, 55, 60, 65, 70, 90, 110]

#Other constants of the PCB board
specificHeatCapacityOfGlass = 0.753 # this in j/g
densityOfGlass = 2.5 #g/cm^3
thermalConductivityOfGlass = 0.8 #W/m, 1 m=100 cm, 1m^(-1)=1/100 cm^(-1)

k = (thermalConductivityOfGlass) / ((specificHeatCapacityOfGlass) * (densityOfGlass))

In [ ]:

#now how to convert this into ∆ deg celsius. 
def lengthMatrix(points):
    return [np.linalg.norm(points[(i+1)%(len(points)),:]-points[i,:]) for i in range(len(points))]

lengthofWires=lengthMatrix(connectorArray)

#plt.show()   

#This function calculates the power (or energy) in each wire on the PCB
def powerMatrix(current, resistanceperKM,points): #this is in milliwatts
    #Step-1: Resistance is ohm/km; So, have a convertion function to make it ohm/cm
    resistanceperKM*=1
    #Step-2: Givent the resistance/cm, calculate the length of each wire-connector; Note: Length in cm
    resistancematrix=[resistanceperKM*i for i in lengthMatrix(points)]
    #Step-3: Calculate the power in each wire ==> P=VI ==> (current)^2 * resistance
    powermatrix=[(current[i]**2*resistancematrix[i]) for i in range(len(resistancematrix)) ]
    return powermatrix #we are given the temperature change in milliwatts, 

matrixForWires=powerMatrix([currentI1,currentI2,currentI3,currentI4], resistanceOfCopperWire,connectorArray) 

#this function models the heat rise in each of the semiconductor chips
heat=lambda x:chipConstant*(1/2+np.arctan(x/4)/np.pi)

#this function converts Power to temperature; 
# Q = (mass) * (specific heat capacity of copper) * (delta-temperature)
# (delta-temperature) = Q * (time) / (mass) * (specific heat capacity of copper)
def heatChange(index,dx,δt):  
    length=lengthofWires[index]
    width=dx / wireThicknessRatio
    height=dx / wireThicknessRatio
    mass=densityOfCopper*length*width*height
    
    #print("***here: ", matrixForWires[index])
    riseInWireTemperature = (δt*matrixForWires[index]) / (specificHeatCopper*mass)
    
    #return δt*matrixForWires[index]*specificHeatCopper*mass
    return riseInWireTemperature

In [ ]:
def initialTemperature(x,y):
    if not(pointInBoundary([x,y],CircuitBoard)):
        return baseTemperature
    else:
        isinSemiConductor=np.array([pointInBoundary([x,y],i) for i in semiconductorList])
        isinConnector=np.array([onEdge([x,y],[connectorArray[i,0],connectorArray[i,1]],
                                       [connectorArray[(i+1)%(len(connectorArray)),0],connectorArray[(i+1)%(len(connectorArray)),1]],tol=5e-2) for i in range(len(connectorArray))])
       # print(isinConnector)
        if (np.array(isinSemiConductor).any()):
            return baseTemperature
        if (np.array(isinConnector).any()):
            return baseTemperature
        return baseTemperature
    
def initializegrid(xlims,ylims,n):
    initialGrid=np.zeros((n+1,n+1))
    for i in range(n+1):
        for j in range(n+1):
            initialGrid[i,j]=initialTemperature(
                xlims[0]+(xlims[1]-xlims[0])/(n)*i,
                ylims[0]+(ylims[1]-ylims[0])/(n)*j
            )         
    return initialGrid


Z_initial=initializegrid([-1,8],[-1,8],100)
#print(Z_initial[100,100])
#print(Z_initial[5:15,5:15])
#fig = plt.figure(figsize=(10,10))
#ax = fig.add_subplot(projection='3d')
#plt.contourf(X, Y, Z_initial, cmap=cm.coolwarm,levels=[15,20,25,30,35,40,45,50], antialiased=True)
#plt.xlabel("y")
#plt.ylabel("x")



In [ ]:
isInSList=lambda l: np.array([pointInBoundary(l,i) for i in semiconductorList ]).any()
isInCListhelper= lambda l:np.array([onEdge(l,[connectorArray[i,0],connectorArray[i,1]],
                                       [connectorArray[(i+1)%(len(connectorArray)),0],connectorArray[(i+1)%(len(connectorArray)),1]],tol=5e-2) for i in range(len(connectorArray))]).any()
isInCList=lambda l:(isInCListhelper(l) and not (isInSList(l)))


In [ ]:
import numpy.random as RNG
from matplotlib import cm
import matplotlib.lines as line
from copy import copy

In [ ]:
from matplotlib.animation import FFMpegWriter
from matplotlib.animation import FuncAnimation
metadata = dict(title='animation', artist='Matplotlib',comment='Lets see if this works')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [ ]:
def doSimulation(δt,finalTime,Z): 
    t=0
    n=Z.shape[0]-1
    η=(δt)/(9/n)**2*k
    T=np.copy(Z)
    fig = plt.figure(dpi=200)
    l=[(i,j) for i in range(1,n) for j in range(1,n) if isInCList([-1+9/n*i,-1+9/n*j])]
    l2=[(i,j) for i in range(1,n) for j in range(1,n) if isInSList([-1+9/n*i,-1+9/n*j])]
    #One time calculations for displaying wires
    massOfWire = [0.0, 0.0, 0.0, 0.0]
    massOfWire[0] = lengthofWires[0] * (9/n) * (9/n) * densityOfCopper # width and height are fixed at (9/n)
    massOfWire[1] = lengthofWires[1] * (9/n) * (9/n) * densityOfCopper
    massOfWire[2] = lengthofWires[2] * (9/n) * (9/n) * densityOfCopper
    massOfWire[3] = lengthofWires[3] * (9/n) * (9/n) * densityOfCopper
    tempOfWire = [0.0, 0.0, 0.0, 0.0]

    x_wire1 = (connectorArray[0,1] + connectorArray[1,1]) / 2
    y_wire1 = (connectorArray[0,0] + connectorArray[1,0]) / 2
    x_wire2 = (connectorArray[1,1] + connectorArray[2,1]) / 2
    y_wire2 = (connectorArray[1,0] + connectorArray[2,0]) / 2
    x_wire3 = (connectorArray[2,1] + connectorArray[3,1]) / 2
    y_wire3 = (connectorArray[2,0] + connectorArray[3,0]) / 2
    x_wire4 = (connectorArray[3,1] + connectorArray[0,1]) / 2
    y_wire4 = (connectorArray[3,0] + connectorArray[0,0]) / 2

    x_wireList = [
        connectorArray[0,0], 
        connectorArray[1,0], 
        connectorArray[2,0], 
        connectorArray[3,0], 
        connectorArray[0,0]]
    y_wireList = [
        connectorArray[0,1], 
        connectorArray[1,1],
        connectorArray[2,1], 
        connectorArray[3,1], 
        connectorArray[0,1]]
    
    wires = line.Line2D(y_wireList, x_wireList,linestyle='-.')
    
    x_chip1List = [ 0.5, 1, 1, 0.5, 0.5]
    y_chip1List = [ 1, 1, 1.5, 1.5, 1]
    chip1 = line.Line2D(y_chip1List, x_chip1List, linestyle='-.')
    
    x_chip2List = [ 5, 5.5, 5.5, 5, 5]
    y_chip2List = [ 1, 1, 1.5, 1.5, 1]
    chip2 = line.Line2D(y_chip2List, x_chip2List, linestyle='-.')
    x_chip3List = [ 5, 5.5, 5.5, 5, 5]
    y_chip3List = [ 3, 3, 3.5, 3.5, 3]
    chip3 = line.Line2D(y_chip3List, x_chip3List, linestyle='-.')
    x_chip4List = [ 2.5, 2.8, 2.8, 2.5, 2.5]
    y_chip4List = [ 2,   2,   2.5, 2.5, 2]
    chip4 = line.Line2D(y_chip4List, x_chip4List, linestyle='-.')

    with writer.saving(fig,"Animation for final project.mp4",dpi=200):
        while (t<=finalTime):
            Tnew=np.copy(T)
           
            
            # Step-1: increase temperature of the wires
             #W=I^2*R comes in to play here
            
            for j in l:
                
                n2=np.array([onEdge([-1+9/n*j[0],-1+9/n*j[1]],[connectorArray[i,0],connectorArray[i,1]],
                                       [connectorArray[(i+1)%(len(connectorArray)),0],connectorArray[(i+1)%(len(connectorArray)),1]],tol=5e-2) for i in range(len(connectorArray))])
                firstindex=np.argmax(n2) #returns which wire a point is in
                #print(firstindex)
                tmpVal = heatChange(firstindex,9/n,δt)
                Tnew[j[0],j[1]] += tmpVal
                tempOfWire[firstindex] = Tnew[j[0],j[1]] + tmpVal
                #print(tmpVal)
            #print([-1+9/n*l[0][0],-1+9/n*l[0][1]])
            #print("the temperature of a wire here is ",Tnew[l[0][0],l[0][1]])
            
            # Step-2: increase chip(s) temperature 
            for i in l2:
                Tnew[i[0],i[1]]=heat(t)
                
            print("chip temperature is ",Tnew[l2[0][0],l2[0][1]])
            
            #Step-3: Calculate the rest of cells in the grid.
            #'''
            for i in range(1,n):
                for j in range(1,n):
                    if not (((i,j) in l) or ((i,j) in l2)):
                        if pointInBoundary([-1+9/n*i,-1+9/n*j],CircuitBoard):
                            Tnew[i,j]=(1-4*η)*T[i,j]+η*(T[i-1,j]+T[i+1,j]+T[i,j+1]+T[i,j-1])
            
            #todo
            #'''
            T=np.copy(Tnew)
            #print(T[n,n])
            #fig.clear()
            fig.clear()
            ax = fig.add_subplot()
            #cs = ax.contourf(X,Y,T,levels=[15,20,25,30,35,40,45,50])
            cs = ax.contourf(X,Y,T,levels=proposedLevels,cmap=cm.Pastel2)
            #plt.xlabel('y[cm]')
            #plt.ylabel('x[cm]') # for some reason boundary(np.array([[0.5,1],[0.5,1.5],[1,1.5],[1,1]]))
            #showed up as a square with vertexes ([1,0.5],[1,1],[1.5,0.5],[1.5,1]) the x and y axes are flipped
            #for some reason, I don't know how to fix it.
            ax.annotate('chip 0', xy = (connectorArray[0,1],connectorArray[0,0]), fontsize=5)
            ax.annotate('chip 1', xy = (connectorArray[1,1],connectorArray[1,0]), fontsize=5)
            ax.annotate('chip 2', xy = (connectorArray[2,1],connectorArray[2,0]), fontsize=5)
            ax.annotate('chip 3', xy = (connectorArray[3,1],connectorArray[3,0]), fontsize=5)
            w1_str = "[1]-L{Len: 2.2f}cm Mass:{Mass: 2.2f}g T:{Temp: 2.2f}c Imax:{Curr: 2.2f}A"
            w2_str = "[2]-L{Len: 2.2f}cm Mass:{Mass: 2.2f}g T:{Temp: 2.2f}c Imax:{Curr: 2.2f}A"
            w3_str = "[3]-L{Len: 2.2f}cm Mass:{Mass: 2.2f}g T:{Temp: 2.2f}c Imax:{Curr: 2.2f}A"
            w4_str = "[4]-L{Len: 2.2f}cm Mass:{Mass: 2.2f}g T:{Temp: 2.2f}c Imax:{Curr: 2.2f}A"
            ax.annotate(
                w1_str.format(Len=lengthofWires[0], Mass=massOfWire[0], Temp=tempOfWire[0], Curr=currentI1), 
                xy = (x_wire1, y_wire1), xytext = (3, -0.5), 
                arrowprops=dict(width=0.05, headwidth=0.05,headlength=0.05,facecolor='black', shrink=0.0005), 
                fontsize=4)
            ax.annotate(w2_str.format(Len=lengthofWires[1], Mass=massOfWire[1], Temp=tempOfWire[1], Curr=currentI2), 
                xy = (x_wire2, y_wire2), xytext = (3,6.5), 
                arrowprops=dict( width=0.05, headwidth=0.05,headlength=0.05,facecolor='black', shrink=0.0005), 
                fontsize=4)
            ax.annotate(w3_str.format(Len=lengthofWires[2], Mass=massOfWire[2], Temp=tempOfWire[2], Curr=currentI3), 
                xy = (x_wire3, y_wire3), xytext = (4,4), 
                arrowprops=dict( width=0.05, headwidth=0.05,headlength=0.05,facecolor='black', shrink=0.0005), 
                fontsize=4)
            ax.annotate(w4_str.format(Len=lengthofWires[3], Mass=massOfWire[3], Temp=tempOfWire[3], Curr=currentI4), 
                xy = (x_wire4, y_wire4), xytext = (3.5,1), 
                arrowprops=dict( width=0.05, headwidth=0.05,headlength=0.05,facecolor='black', shrink=0.0005), 
                fontsize=4)
            wires_c = copy(wires)
            ax.add_line(wires_c)
            chip1_c = copy(chip1)
            ax.add_line(chip1_c)
            chip2_c = copy(chip2)
            ax.add_line(chip2_c)
            chip3_c = copy(chip3)
            ax.add_line(chip3_c)
            chip4_c = copy(chip4)
            ax.add_line(chip4_c)
            #plt.plot(y_wireList, x_wireList, marker='o')
                
            ax.set_xlabel('y[cm]')
            ax.set_ylabel('x[cm]')
            cb=plt.colorbar(cs)
            cb.set_label('temperature[°celcius]')
            #timeString='temperature distribution at t='+str(t)
            timeString = "Temp Distribution at {Time: 2.4f}"
            #print(timeString.format(Time=t))
            fig.suptitle(timeString.format(Time=t))
            plt.show()
            plt.pause(0.05)
            writer.grab_frame()
            #fig.clear()
            t+=δt
            
            print(t)

dt=((9/100))**2/(8*k)
print(dt)
#i'm making sure that η=1/8 here, so that its stable. η=k*∆t/(∆x)^2, ∆x=9/100, so δt=(∆x)^2/(8k). 
#remember that if η>1/4, this equation becomes unstable 
doSimulation(dt,2,Z_initial)    
